In [1]:
import xarray as xr
import cdsapi

In [2]:
client = cdsapi.Client()

In [3]:
dx = 2.
grid = [dx, dx]
area = [90-dx/2, -180+dx/2, -90+dx/2, 180]
year = ['{}'.format(y) for y in range(1979, 2025)]
month = ['{:02d}'.format(m) for m in range(1, 13)]

In [4]:
dl_dir = 'tmp/'

## Invariant

In [5]:
filename = 'ERA5_UltraLowRes_Invariant.nc'
dataset = "reanalysis-era5-single-levels-monthly-means"
request = {
    "product_type": ["monthly_averaged_reanalysis"],
    "variable": [
        "geopotential",
        "land_sea_mask"
    ],
    "grid": grid,
    "area": area,
    "year": ["1979"],
    "month": ["01"],
    "time": ["00:00"],
    "data_format": "netcdf",
    "download_format": "unarchived",
}

client.retrieve(dataset, request).download(dl_dir + filename)
print('+++ Done!')

2025-11-27 13:46:20,204 INFO Request ID is 760003cc-ce59-44a1-bf87-f202e4c4a420
2025-11-27 13:46:20,350 INFO status has been updated to accepted
2025-11-27 13:47:10,974 INFO status has been updated to successful
                                                                                                                                                                                                   

FileNotFoundError: [Errno 2] No such file or directory: 'tmp/ERA5_UltraLowRes_Invariant.nc'

In [16]:
# Unfortunate necessary cleaning
with xr.open_dataset(dl_dir + filename) as ds:
    # ds = ds.rename({"valid_time": "time"}).drop_vars(["expver", "number"]) #, errors="ignore")
    
    ds = ds.isel(valid_time=0).drop_vars(["expver", "number", "valid_time"])
    ds['orography'] = ds['z']  / 9.80665
    ds['orography'].attrs.update(long_name='Orography', units='m', standard_name='orography')
    ds = ds.drop_vars(["z"])
    ds['lsm'].attrs = {k: v for k, v in ds['lsm'].attrs.items() if not k.startswith("GRIB_")}
    
    ds.attrs = {k: v for k, v in ds.attrs.items() if not k.startswith("GRIB_")}
    ds.to_netcdf(filename)

## Temp and precip 

In [17]:
filename = 'ERA5_UltraLowRes_Monthly_t2m.nc'

dataset = "reanalysis-era5-single-levels-monthly-means"
request = {
    "product_type": ["monthly_averaged_reanalysis"],
    "variable": ["2m_temperature"],
    "grid": grid,
    "area": area,
    "year": year,
    "month": month,
    "time": ["00:00"],
    "data_format": "netcdf",
    "download_format": "unarchived",
}

client.retrieve(dataset, request).download(dl_dir + filename)
print('+++ Done!')

2025-02-06 15:26:29,582 INFO Request ID is d754fd9e-9084-45c6-b931-876995a832ea
2025-02-06 15:26:29,663 INFO status has been updated to accepted
2025-02-06 15:26:37,090 INFO status has been updated to running
2025-02-06 15:27:22,869 WARNING Structural differences in grib fields detected when opening in xarray. Opening the grib file safely, however this may result in files with non-intuitive filenames.
2025-02-06 15:27:22,870 INFO status has been updated to successful


c6d1df5982f73d62909439fdb3d153b5.nc:   0%|          | 0.00/15.7M [00:00<?, ?B/s]

+++ Done!


In [18]:
# Unfortunate necessary cleaning
with xr.open_dataset(dl_dir + filename) as ds:
    ds = ds.rename({"valid_time": "time"}).drop_vars(["expver", "number"]) 
     
    ds.attrs = {k: v for k, v in ds.attrs.items() if not k.startswith("GRIB_")}
    for var in ds.variables.keys():
        ds[var].attrs = {k: v for k, v in ds[var].attrs.items() if not k.startswith("GRIB_")}
    
    ds.to_netcdf(filename)

In [19]:
filename = 'ERA5_UltraLowRes_Monthly_tp.nc'

dataset = "reanalysis-era5-single-levels-monthly-means"
request = {
    "product_type": ["monthly_averaged_reanalysis"],
    "variable": ["total_precipitation"],
    "grid": grid,
    "area": area,
    "year": year,
    "month": month,
    "time": ["00:00"],
    "data_format": "netcdf",
    "download_format": "unarchived",
}

client.retrieve(dataset, request).download(dl_dir + filename)
print('+++ Done!')

2025-02-06 15:27:25,170 INFO Request ID is 1747df94-461a-4ffc-b159-39fb36daa332
2025-02-06 15:27:25,246 INFO status has been updated to accepted
2025-02-06 15:27:34,529 INFO status has been updated to running
2025-02-06 15:29:20,819 WARNING Structural differences in grib fields detected when opening in xarray. Opening the grib file safely, however this may result in files with non-intuitive filenames.
2025-02-06 15:29:20,820 INFO status has been updated to successful


7232e3eeccf7fdc5235eede62a2fdb54.nc:   0%|          | 0.00/15.2M [00:00<?, ?B/s]

+++ Done!


In [20]:
# Unfortunate necessary cleaning
with xr.open_dataset(dl_dir + filename) as ds:
    ds = ds.rename({"valid_time": "time"}).drop_vars(["expver", "number"]) 
     
    ds.attrs = {k: v for k, v in ds.attrs.items() if not k.startswith("GRIB_")}
    for var in ds.variables.keys():
        ds[var].attrs = {k: v for k, v in ds[var].attrs.items() if not k.startswith("GRIB_")}
    
    ds.to_netcdf(filename)